# Nettverksanalyse i sgis
https://github.com/statisticsnorway/ssb-sgis

Notebook-en kan kjøres i dapla hvis man har tilgang til bøtta 'kart'.

Eller åpnes her: https://nbviewer.org/github/statisticsnorway/intro_til_geopandas/blob/main/brukerforum_20_04_2022/nettverksanalyse.ipynb

In [23]:
# poetry add ssb-sgis


Poetry could not find a pyproject.toml file in /home/jovyan/intro_til_geopandas/brukerforum_20_04_2022 or its parents


In [2]:
import numpy as np
import sgis as sg

## Hente vegdata

Henter vegdata i Oslo for 2022 med relevante kolonner: retning og kjøretid.

In [3]:
aar = 2022
kommnr = "0301"

In [4]:
kartdata = "ssb-prod-kart-data-delt/kartdata_analyse/klargjorte-data"

veger_oslo = (
    sg.read_geopandas(
        f"{kartdata}/2022/NVDB_ruteplan_nettverk_p20220703_v1.parquet",
        filters=[f"KOMMUNENR = {kommnr}".split()],
        columns=["oneway", "drivetime_fw", "drivetime_bw", "geometry"]
    )
    .sort_values("oneway")
    .reset_index(drop=True)
)

veger_oslo

oneway  drivetime_fw  drivetime_bw  \
0          B      0.216611      0.216611   
1          B      0.064631      0.064631   
2          B      0.023387      0.023387   
3          B      0.174470      0.174470   
4          B      0.085934      0.085934   
...      ...           ...           ...   
93390     TF     -1.000000      0.003683   
93391     TF     -1.000000      0.031986   
93392     TF     -1.000000      0.010607   
93393     TF     -1.000000      0.004257   
93394     TF     -1.000000      0.128560   

                                                geometry  
0      MULTILINESTRING Z ((258028.440 6674249.890 413...  
1      MULTILINESTRING Z ((263329.703 6652880.398 88....  
2      MULTILINESTRING Z ((270274.700 6651212.900 154...  
3      MULTILINESTRING Z ((267240.000 6644124.500 133...  
4      MULTILINESTRING Z ((273365.300 6652133.100 174...  
...                                                  ...  
93390  MULTILINESTRING Z ((263871.009 6648498.376 29....  
93391  MULTILINESTRING Z ((267727.200 6649124.300 155...  
93392  MULTILINESTRING Z ((263871.400 6648500.800 29....  
93393  MULTILINESTRING Z ((256561.560 6651007.630 63....  
93394  MULTILINESTRING Z ((262522.672 6651527.844 52....  

[93395 rows x 4 columns]

## Gjør klar til nettverksanalyse

Starter med å definere noen regler for analysene.

Her vil jeg beregne kjøretid med bil. Setter derfor vekt-kolonnen til "minutes" og directed til True (som betyr at man bare kan bevege seg i én retning langs vegene).

In [5]:
regler = sg.NetworkAnalysisRules(
    weight="minutes",
    directed=True,
    search_tolerance=500, # meter
)
regler

NetworkAnalysisRules(directed=True, weight='minutes', search_tolerance=500, search_factor=0, split_lines=False, nodedist_multiplier=None, nodedist_kmh=None)

For å få et vegnett der alle veger går i riktig retning, må man snu vegene som går i motsatt/begge retning(er).

In [6]:
antall_per_retning = veger_oslo.oneway.value_counts().to_frame()

antall_per_retning["hva_må_gjøres"] = {"B": "Duplisere og snu duplikatene", "TF": "Snu", "FT": "Ingenting"}

antall_per_retning

oneway                 hva_må_gjøres
B    82230  Duplisere og snu duplikatene
FT    7353                     Ingenting
TF    3812                           Snu

Og man må lage en felles minutt-kolonne av kjøretid-kolonnene.

In [7]:
veger_oslo[["oneway", "drivetime_fw", "drivetime_bw"]]

oneway  drivetime_fw  drivetime_bw
0          B      0.216611      0.216611
1          B      0.064631      0.064631
2          B      0.023387      0.023387
3          B      0.174470      0.174470
4          B      0.085934      0.085934
...      ...           ...           ...
93390     TF     -1.000000      0.003683
93391     TF     -1.000000      0.031986
93392     TF     -1.000000      0.010607
93393     TF     -1.000000      0.004257
93394     TF     -1.000000      0.128560

[93395 rows x 3 columns]

Dette kan gjøres sånn her:

In [8]:
veger_med_retning = sg.make_directed_network_norway(veger_oslo)
veger_med_retning

oneway   minutes                                           geometry
0           B  0.216611  MULTILINESTRING Z ((258028.440 6674249.890 413...
1           B  0.064631  MULTILINESTRING Z ((263329.703 6652880.398 88....
2           B  0.023387  MULTILINESTRING Z ((270274.700 6651212.900 154...
3           B  0.174470  MULTILINESTRING Z ((267240.000 6644124.500 133...
4           B  0.085934  MULTILINESTRING Z ((273365.300 6652133.100 174...
...       ...       ...                                                ...
175620     TF  0.003683  MULTILINESTRING Z ((263871.400 6648500.800 29....
175621     TF  0.031986  MULTILINESTRING Z ((267749.000 6649137.700 156...
175622     TF  0.010607  MULTILINESTRING Z ((263874.800 6648507.000 29....
175623     TF  0.004257  MULTILINESTRING Z ((256560.200 6651010.200 63....
175624     TF  0.128560  MULTILINESTRING Z ((262543.865 6651593.052 54....

[175541 rows x 3 columns]

Eller en mer generell variant:

In [9]:
veger_med_retning = sg.make_directed_network(
    veger_oslo,
    direction_col="oneway",
    direction_vals_bft=("B", "FT", "TF"),
    minute_cols=("drivetime_fw", "drivetime_bw"),
)

veger_med_retning

oneway   minutes                                           geometry
0           B  0.216611  MULTILINESTRING Z ((258028.440 6674249.890 413...
1           B  0.064631  MULTILINESTRING Z ((263329.703 6652880.398 88....
2           B  0.023387  MULTILINESTRING Z ((270274.700 6651212.900 154...
3           B  0.174470  MULTILINESTRING Z ((267240.000 6644124.500 133...
4           B  0.085934  MULTILINESTRING Z ((273365.300 6652133.100 174...
...       ...       ...                                                ...
175620     TF  0.003683  MULTILINESTRING Z ((263871.400 6648500.800 29....
175621     TF  0.031986  MULTILINESTRING Z ((267749.000 6649137.700 156...
175622     TF  0.010607  MULTILINESTRING Z ((263874.800 6648507.000 29....
175623     TF  0.004257  MULTILINESTRING Z ((256560.200 6651010.200 63....
175624     TF  0.128560  MULTILINESTRING Z ((262543.865 6651593.052 54....

[175541 rows x 3 columns]

In [10]:
print("Kilometer før:", veger_oslo.length.sum() / 1000)
print("Kilometer nå:", veger_med_retning.length.sum() / 1000)

Kilometer før: 3851.4819685472407
Kilometer nå: 7248.592623912765


In [11]:
veger_med_retning.minutes

0         0.216611
1         0.064631
2         0.023387
3         0.174470
4         0.085934
            ...   
175620    0.003683
175621    0.031986
175622    0.010607
175623    0.004257
175624    0.128560
Name: minutes, Length: 175541, dtype: float64

Man bør også fjerne isolerte nettverksøyer. Dette er gjerne veger bak bommer (innkjørsler, inni borettslag).

Sånn her kan man finne og fjerne nettverksøyene:

In [12]:
veger_ned_tilknytning = sg.get_connected_components(veger_med_retning).query("connected == 1")
veger_ned_tilknytning

oneway   minutes                                           geometry  \
1           B  0.064631  LINESTRING Z (263329.703 6652880.398 88.022, 2...   
3           B  0.174470  LINESTRING Z (267240.000 6644124.500 133.461, ...   
4           B  0.085934  LINESTRING Z (273365.300 6652133.100 174.571, ...   
5           B  0.119831  LINESTRING Z (273398.500 6651934.000 163.171, ...   
6           B  0.050873  LINESTRING Z (263319.400 6652894.300 87.962, 2...   
...       ...       ...                                                ...   
175620     TF  0.003683  LINESTRING Z (263871.400 6648500.800 29.259, 2...   
175621     TF  0.031986  LINESTRING Z (267749.000 6649137.700 156.064, ...   
175622     TF  0.010607  LINESTRING Z (263874.800 6648507.000 29.759, 2...   
175623     TF  0.004257  LINESTRING Z (256560.200 6651010.200 63.654, 2...   
175624     TF  0.128560  LINESTRING Z (262543.865 6651593.052 54.090, 2...   

        connected  
1             1.0  
3             1.0  
4             1.0  
5             1.0  
6             1.0  
...           ...  
175620        1.0  
175621        1.0  
175622        1.0  
175623        1.0  
175624        1.0  

[160137 rows x 4 columns]

In [14]:
print("Kilometer før:", veger_med_retning.length.sum() / 1000)
print("Kilometer nå:", veger_ned_tilknytning.length.sum() / 1000)

Kilometer før: 7248.592623912765
Kilometer nå: 6364.053626251761


In [15]:
sg.samplemap(veger_med_retning, veger_ned_tilknytning)

Nå er vegene klare for nettverksanalyse:

In [16]:
nwa = sg.NetworkAnalysis(network=veger_ned_tilknytning, rules=regler)
nwa

NetworkAnalysis(
    network=Network(6364 km, percent_bidirectional=87),
    rules=NetworkAnalysisRules(weight=minutes, directed=True, search_tolerance=500, search_factor=0, split_lines=False, ...),
    log=True, detailed_log=False,
)

### Først en liten test av retning
La oss teste at retningen lages riktig.

Sjekker at tur-retur Vippetangen-Ryen går i riktige tunnelløp.

In [17]:
vippetangen = sg.to_gdf([10.741527, 59.9040595], crs=4326).to_crs(veger_oslo.crs)
ryen = sg.to_gdf([10.8047522, 59.8949826], crs=4326).to_crs(veger_oslo.crs)

OBS: Å beregne én rute av gangen går mye treigere enn å beregne mange samtidig.

In [18]:
ryen_til_vippa = nwa.get_route(ryen, vippetangen)
vippa_til_ryen = nwa.get_route(vippetangen, ryen)
sg.explore(ryen_til_vippa, vippa_til_ryen)

### Reisetider: OD Cost Matrix

Henter bygningspunkter i Oslo for 2022.

In [19]:
bygningspunktsti = f"ssb-prod-kart-data-delt/kartdata_analyse/klargjorte-data/{aar}/SMAT_bygg_punkt_p{aar}_v1.parquet"

bygg_oslo = sg.read_geopandas(
    bygningspunktsti,
    filters=[(f"KOMMUNENR", "=", kommnr)],
    columns=["geometry"]
)
bygg_oslo

geometry
2295777  POINT (266589.000 6638437.000)
2295778  POINT (266732.000 6638437.000)
2295785  POINT (268985.000 6638438.000)
2295807  POINT (268630.000 6638490.000)
2295816  POINT (266745.000 6638491.000)
...                                 ...
2704094  POINT (258558.000 6667933.000)
2704589  POINT (258492.000 6667941.000)
2704605  POINT (258532.000 6668042.000)
2704777  POINT (256610.000 6668631.000)
2704846  POINT (256158.000 6668920.000)

[132266 rows x 1 columns]

Lager 1000 start- og sluttpunkter.

In [20]:
origins = bygg_oslo.sample(1000)
origins.index = np.arange(0, 1000)
origins

geometry
0    POINT (256455.000 6656968.000)
1    POINT (264465.000 6643312.000)
2    POINT (273281.000 6653144.000)
3    POINT (266893.000 6644467.000)
4    POINT (257893.000 6651251.000)
..                              ...
995  POINT (272882.000 6652911.000)
996  POINT (266596.000 6645624.000)
997  POINT (267575.000 6648637.000)
998  POINT (273099.000 6652075.000)
999  POINT (256656.000 6653029.000)

[1000 rows x 1 columns]

In [21]:
destinations = bygg_oslo.sample(1000)
destinations.index = np.arange(1000, 2000)
destinations

geometry
1000  POINT (268160.000 6647125.000)
1001  POINT (267332.000 6646195.000)
1002  POINT (271892.000 6652770.000)
1003  POINT (259047.000 6654348.000)
1004  POINT (259310.000 6652881.000)
...                              ...
1995  POINT (265048.000 6642463.000)
1996  POINT (265377.000 6644307.000)
1997  POINT (265668.000 6645931.000)
1998  POINT (258926.000 6654814.000)
1999  POINT (260116.000 6653594.000)

[1000 rows x 1 columns]

Og beregner reisetid mellom dem:

In [22]:
od = nwa.od_cost_matrix(
    origins,
    destinations,
)

od

origin  destination    minutes
0            0         1000  28.904348
1            0         1001  28.907799
2            0         1002  31.825359
3            0         1003  12.711784
4            0         1004  13.493222
...        ...          ...        ...
999995     999         1995  23.241526
999996     999         1996  20.436899
999997     999         1997  23.164328
999998     999         1998   8.946449
999999     999         1999   8.988744

[1000000 rows x 3 columns]

La oss undersøke hvilke punkter som har mye manglende data. 

In [ ]:
antall_som_ikke_mangler = od.groupby("origin", dropna=False).minutes.count()
origins["n_missing"] = len(origins) - antall_som_ikke_mangler
origins

In [ ]:
origins.n_missing.value_counts()

In [ ]:
# gjør kolonnen til tekst for å kunne huke av/på verdiene i explore
origins["n_missing_cat"] = origins.n_missing.astype(str)
sg.explore(origins, column="n_missing_cat")

Med lines=True får man rette linjer, så man lettere kan undersøke resultatene.

In [ ]:
od = nwa.od_cost_matrix(
    origins.sample(1),
    destinations,
    lines=True
)

m = sg.ThematicMap(od, column="minutes", size=15)
m.black = True
m.title = "Reisetid fra 1 til 1000 adresser"
m.legend.title = "Minutter"
m.scheme = "quantiles"
m.plot()

Sjekke loggen:

In [ ]:
nwa.log